In [82]:
import numpy as np
import open3d as o3d
from sklearn.neighbors import KDTree
import time
import math

In [2]:
# Read pointcloud
input_file = "./Pointclouds/tre-pc1.ply"
pcd = o3d.io.read_point_cloud(input_file) # Read the point cloud

# Convert to pointcloud
np_pc = np.asarray(pcd.points) 

In [ ]:
# Visualize pointcloud
o3d.visualization.draw_geometries([pcd])

In [3]:
# Find unique points
pc = np.unique(np_pc, axis=0)
print(len(pc))

490246


In [ ]:
from collections import namedtuple
from operator import itemgetter
from pprint import pformat

class Node(namedtuple("Node", "location left_child right_child")):
    def __repr__(self):
        return pformat(tuple(self))

def kdtree(point_list, depth: int = 0):
    if not point_list:
        return None
    k = len(point_list[0])  # assumes all points have the same dimension
    # Select axis based on depth so that axis cycles through all valid values
    axis = depth % k

    # Sort point list by axis and choose median as pivot element
    point_list.sort(key=itemgetter(axis))
    median = len(point_list) // 2

    # Create node and construct subtrees
    return Node(
        location=point_list[median],
        left_child=kdtree(point_list[:median], depth + 1),
        right_child=kdtree(point_list[median + 1 :], depth + 1),
    )

"""Example usage"""
point_list = list(map(tuple, pc))
tree = kdtree(point_list, 50)


In [12]:
start_time = time.time()
tree = KDTree(pc, leaf_size=1000)
print("--- %s seconds ---" % (time.time() - start_time))

--- 165.26704692840576 seconds ---


In [9]:
print(pc[:5])

[[-4.0335836   0.26610637 -0.11068945]
 [-4.022581    0.26616907 -0.13173483]
 [-4.01972     0.31380525 -0.08591751]
 [-4.018031    0.29089716 -0.10870852]
 [-4.01281     0.31270027 -0.10705944]]


In [27]:
start_time = time.time()
dist, ind = tree.query(pc, k=100)  
print("--- %s seconds ---" % (time.time() - start_time))

--- 25.413565158843994 seconds ---


In [74]:
normals = []
curvatures = []

start_time = time.time()

for idxs in ind:
    points = pc[idxs]
    
    x_hat = 1/len(points) * sum(points[:, 0])
    y_hat = 1/len(points) * sum(points[:, 1])
    z_hat = 1/len(points) * sum(points[:, 2])
    
    M = np.zeros((len(points), 3))
    M[:, 0] = points[:, 0] - x_hat
    M[:, 1] = points[:, 1] - y_hat
    M[:, 2] = points[:, 2] - z_hat
    
    C_norm = M.transpose() @ M
    eigenvalue1 = C_norm[0,0]
    eigenvalue2 = C_norm[1,1]
    eigenvalue3 = C_norm[2,2]
    
    eigen_vals, eigen_vecs = np.linalg.eigh(C_norm)
    
    n = eigen_vecs[0]
    c = eigen_vals[0]/(np.sqrt(eigen_vals[0]**2 + eigen_vals[1]**2 + eigen_vals[2]**2))
    
    normals.append(list(n))
    curvatures.append(c)
normals=np.array(normals)
curvatures=np.array(curvatures)
print("--- %s seconds ---" % (time.time() - start_time))

--- 27.218154430389404 seconds ---


In [91]:
# Combine points into one dict
pc_dict = []

for i, p in enumerate(pc):
    pc_dict.append({"position": p, "n": normals[i], "c": curvatures[i], "s": 0.0, "idx": i})
    

print(pc_dict[0])

{'position': array([-4.0335836 ,  0.26610637, -0.11068945]), 'n': array([0.75296464, 0.41403716, 0.51148557]), 'c': 0.007320789697269496, 's': 0.0, 'idx': 0}


In [119]:
# KNN for next step
start_time = time.time()
dist2, ind2 = tree.query(pc, k=10)
print("--- Sort by height: %s seconds ---" % (time.time() - start_time))

--- Sort by height: 12.56910228729248 seconds ---


In [120]:
def unit_vector(vector):
    """ Returns the unit vector of the vector.  """
    return vector / np.linalg.norm(vector)

def angle_between(v1, v2):
    """ Returns the angle in degrees between vectors 'v1' and 'v2'::

            >>> angle_between((1, 0, 0), (0, 1, 0))
            1.5707963267948966
            >>> angle_between((1, 0, 0), (1, 0, 0))
            0.0
            >>> angle_between((1, 0, 0), (-1, 0, 0))
            3.141592653589793
    """
    v1_u = unit_vector(v1)
    v2_u = unit_vector(v2)
    rad = np.arccos(np.clip(np.dot(v1_u, v2_u), -1.0, 1.0))
    return rad * 180.0 / math.pi 

In [121]:
print(max(curvatures), min(curvatures))

0.5574220205542895 1.3455342068558392e-05


In [124]:
SQ=[]
region = []
S_threshold = 20.0
c_threshold = 0.00005

# 1.1 Sort by height
start_time = time.time()
pc_dict_sort = sorted(pc_dict, key=lambda d: d['position'][2]) 
print("--- Sort by height: %s seconds ---" % (time.time() - start_time))

# 1.2 Sort by curvature
start_time = time.time()
pc_dict_sort = sorted(pc_dict, key=lambda d: d['c']) 
print("--- Sort by curvature: %s seconds ---" % (time.time() - start_time))

# 1.3 Determine seed point A with low height and the smallest curvature
A=pc_dict_sort[0]

SQ.append(A)

while(len(SQ) > 0):
    
    A = SQ[0]
    print(A)
    regions.append(A)
    
    # 2.1 Search knn of the seed A
    knn = [pc_dict[i] for i in ind2[A["idx"]]]

    # 2.2 Calculate angle S_i between normal vectors of each neighbor point B_i and A
    for p in knn:
        p["s"] = angle_between(A['n'], p['n'])

    # 3.1 If angle Si satisfies S_i < S_threshold => add B_i to region where A is located
    # 3.2 If curvature c_i of B_i satisfies c_i < c_threshold => add B_i to seed queue SQ as new candidate seed point
    for p in knn:
        if p["s"] < S_threshold:
            region.append(p)

        if p['c'] < c_threshold:
            SQ.append(p)

    print("# points in region: ", len(region))

    # 4.1 Dequeue A from SQ. If SQ not empty, select new seed point and return step 2.1
    SQ.pop(0)

    print("SQ: ", len(SQ))
    print("------------ end of loop ----------------")

--- Sort by height: 0.32102274894714355 seconds ---
--- Sort by curvature: 0.38899731636047363 seconds ---
{'position': array([ 0.39951098,  0.98626155, -0.4698206 ]), 'n': array([ 0.75883728,  0.16673987, -0.6295743 ]), 'c': 1.3455342068558392e-05, 's': 0.0, 'idx': 198260}
# points in region:  7
SQ:  10
------------ end of loop ----------------
{'position': array([ 0.39951098,  0.98626155, -0.4698206 ]), 'n': array([ 0.75883728,  0.16673987, -0.6295743 ]), 'c': 1.3455342068558392e-05, 's': 0.0, 'idx': 198260}
# points in region:  14
SQ:  19
------------ end of loop ----------------
{'position': array([ 0.39839062,  0.98747474, -0.46579203]), 'n': array([ 0.75889754,  0.14766222, -0.63424789]), 'c': 1.3940070527526048e-05, 's': 1.12541382793171, 'idx': 198063}
# points in region:  22
SQ:  28
------------ end of loop ----------------
{'position': array([ 0.40061656,  0.98505586, -0.4738607 ]), 'n': array([ 0.75864628,  0.38018073, -0.52907318]), 'c': 1.5514089852301303e-05, 's': 14.6618

{'position': array([ 0.39839062,  0.98747474, -0.46579203]), 'n': array([ 0.75889754,  0.14766222, -0.63424789]), 'c': 1.3940070527526048e-05, 's': 1.12541382793171, 'idx': 198063}
# points in region:  872
SQ:  1212
------------ end of loop ----------------
{'position': array([ 0.40245637,  0.9828296 , -0.4822338 ]), 'n': array([ 0.75886876,  0.27378721, -0.59089658]), 'c': 2.0361656167028932e-05, 's': 79.57900409546119, 'idx': 198774}
# points in region:  879
SQ:  1221
------------ end of loop ----------------
{'position': array([ 0.3935665 ,  0.9934998 , -0.47690377]), 'n': array([ 0.75929012, -0.63387314,  0.14725269]), 'c': 1.6458569194375275e-05, 's': 67.80381002417508, 'idx': 197208}
# points in region:  882
SQ:  1230
------------ end of loop ----------------
{'position': array([ 0.40776357,  0.97669417, -0.4706783 ]), 'n': array([ 0.75802543,  0.20269129, -0.61993039]), 'c': 1.4353925945136188e-05, 's': 2.1333185109155632, 'idx': 199714}
# points in region:  890
SQ:  1239
------

# points in region:  1641
SQ:  2270
------------ end of loop ----------------
{'position': array([ 0.39767224,  0.98848546, -0.46146065]), 'n': array([ 0.75903943,  0.11076308, -0.64155333]), 'c': 1.3838186132587167e-05, 's': 3.446134793141239, 'idx': 197926}
# points in region:  1649
SQ:  2279
------------ end of loop ----------------
{'position': array([ 0.39429763,  0.9921307 , -0.44939277]), 'n': array([ 0.76002469, -0.03417759, -0.64899489]), 'c': 2.0157564355343897e-05, 's': 4.88303046301675, 'idx': 197335}
# points in region:  1656
SQ:  2288
------------ end of loop ----------------
{'position': array([ 0.39839062,  0.98747474, -0.46579203]), 'n': array([ 0.75889754,  0.14766222, -0.63424789]), 'c': 1.3940070527526048e-05, 's': 2.1553444924127008, 'idx': 198063}
# points in region:  1664
SQ:  2297
------------ end of loop ----------------
{'position': array([ 0.38900337,  0.99842894, -0.46058694]), 'n': array([ 0.76005458, -0.38197782, -0.52574707]), 'c': 1.988665101720056e-05, 

# points in region:  2446
SQ:  3361
------------ end of loop ----------------
{'position': array([ 0.41452828,  0.96864927, -0.46773016]), 'n': array([ 0.75737212, -0.04080076, -0.65170758]), 'c': 1.658625724843814e-05, 's': 71.04766419421615, 'idx': 200947}
# points in region:  2454
SQ:  3370
------------ end of loop ----------------
{'position': array([ 0.40061656,  0.98505586, -0.4738607 ]), 'n': array([ 0.75864628,  0.38018073, -0.52907318]), 'c': 1.5514089852301303e-05, 's': 80.53434246864423, 'idx': 198456}
# points in region:  2461
SQ:  3379
------------ end of loop ----------------
{'position': array([ 0.41384256,  0.9696325 , -0.46349484]), 'n': array([ 0.75732903,  0.14616296, -0.63646613]), 'c': 1.699924309871063e-05, 's': 10.763588885422493, 'idx': 200809}
# points in region:  2470
SQ:  3388
------------ end of loop ----------------
{'position': array([ 0.40173727,  0.98384243, -0.4778892 ]), 'n': array([ 0.75877547, -0.47062962,  0.45029718]), 'c': 1.6691561110239635e-05, 

SQ:  4420
------------ end of loop ----------------
{'position': array([ 0.41064715,  0.97331613, -0.48294532]), 'n': array([ 0.75839849,  0.3580354 , -0.54464887]), 'c': 2.643687044869769e-05, 's': 17.691723956618258, 'idx': 200249}
# points in region:  3266
SQ:  4428
------------ end of loop ----------------
{'position': array([ 0.40776357,  0.97669417, -0.4706783 ]), 'n': array([ 0.75802543,  0.20269129, -0.61993039]), 'c': 1.4353925945136188e-05, 's': 7.8655454910853475, 'idx': 199714}
# points in region:  3274
SQ:  4437
------------ end of loop ----------------
{'position': array([ 0.41174006,  0.97212505, -0.48693246]), 'n': array([ 0.75851022,  0.41500954, -0.50242345]), 'c': 4.16791674437626e-05, 's': 4.064028402482928, 'idx': 200450}
# points in region:  3284
SQ:  4442
------------ end of loop ----------------
{'position': array([ 0.416679  ,  0.96630204, -0.475599  ]), 'n': array([ 0.75733087,  0.32095558, -0.56871562]), 'c': 1.8830731784847533e-05, 's': 2.5337304536471876, '

...

# points in region:  96729
SQ:  124085
------------ end of loop ----------------
{'position': array([ 0.40245637,  0.9828296 , -0.4822338 ]), 'n': array([ 0.75886876,  0.27378721, -0.59089658]), 'c': 2.0361656167028932e-05, 's': 79.57900409546119, 'idx': 198774}
# points in region:  96736
SQ:  124094
------------ end of loop ----------------
{'position': array([ 0.40245637,  0.9828296 , -0.4822338 ]), 'n': array([ 0.75886876,  0.27378721, -0.59089658]), 'c': 2.0361656167028932e-05, 's': 0.0, 'idx': 198774}
# points in region:  96743
SQ:  124103
------------ end of loop ----------------
{'position': array([ 0.40356436,  0.98162216, -0.48627514]), 'n': array([ 0.75918849,  0.33435958, -0.55842324]), 'c': 3.355172354597031e-05, 's': 3.938639022876464, 'idx': 198978}
# points in region:  96751
SQ:  124110
------------ end of loop ----------------
{'position': array([ 0.40173727,  0.98384243, -0.4778892 ]), 'n': array([ 0.75877547, -0.47062962,  0.45029718]), 'c': 1.6691561110239635e-05, 's

{'position': array([ 0.39767224,  0.98848546, -0.46146065]), 'n': array([ 0.75903943,  0.11076308, -0.64155333]), 'c': 1.3838186132587167e-05, 's': 3.2803194270471554, 'idx': 197926}
# points in region:  97627
SQ:  125156
------------ end of loop ----------------
{'position': array([ 0.3965525 ,  0.9896979 , -0.45743424]), 'n': array([ 0.75932015,  0.07847769, -0.64596762]), 'c': 1.50365139868024e-05, 's': 1.8671789073323488, 'idx': 197758}
# points in region:  97634
SQ:  125165
------------ end of loop ----------------
{'position': array([ 0.39839062,  0.98747474, -0.46579203]), 'n': array([ 0.75889754,  0.14766222, -0.63424789]), 'c': 1.3940070527526048e-05, 's': 4.021352355707489, 'idx': 198063}
# points in region:  97642
SQ:  125174
------------ end of loop ----------------
{'position': array([ 0.39541626,  0.99091876, -0.45342013]), 'n': array([ 0.75959588,  0.05101836, -0.64839126]), 'c': 1.7405497433985438e-05, 's': 1.5795493414899064, 'idx': 197545}
# points in region:  97649
S

SQ:  126255
------------ end of loop ----------------
{'position': array([ 0.40245637,  0.9828296 , -0.4822338 ]), 'n': array([ 0.75886876,  0.27378721, -0.59089658]), 'c': 2.0361656167028932e-05, 's': 79.57900409546119, 'idx': 198774}
# points in region:  98608
SQ:  126264
------------ end of loop ----------------
{'position': array([ 0.4099584 ,  0.97430825, -0.47863895]), 'n': array([ 0.75828052,  0.29753407, -0.58007252]), 'c': 1.8426869028471003e-05, 's': 1.4956924334859834, 'idx': 200100}
# points in region:  98618
SQ:  126273
------------ end of loop ----------------
{'position': array([ 0.40885377,  0.9755048 , -0.4746643 ]), 'n': array([ 0.75823297,  0.0685012 , -0.64837517]), 'c': 1.546101785079858e-05, 's': 13.726531511318965, 'idx': 199910}
# points in region:  98626
SQ:  126282
------------ end of loop ----------------
{'position': array([ 0.41064715,  0.97331613, -0.48294532]), 'n': array([ 0.75839849,  0.3580354 , -0.54464887]), 'c': 2.643687044869769e-05, 's': 17.691723

# points in region:  99651
SQ:  127423
------------ end of loop ----------------
{'position': array([ 0.41206825,  0.9717943 , -0.4553467 ]), 'n': array([ 0.75731971,  0.05328281, -0.65086697]), 'c': 1.8379554325226296e-05, 's': 2.2729729811534796, 'idx': 200497}
# points in region:  99659
SQ:  127432
------------ end of loop ----------------
{'position': array([ 0.39839062,  0.98747474, -0.46579203]), 'n': array([ 0.75889754,  0.14766222, -0.63424789]), 'c': 1.3940070527526048e-05, 's': 16.317041029344857, 'idx': 198063}
# points in region:  99667
SQ:  127441
------------ end of loop ----------------
{'position': array([ 0.41384256,  0.9696325 , -0.46349484]), 'n': array([ 0.75732903,  0.14616296, -0.63646613]), 'c': 1.699924309871063e-05, 's': 5.387210573786099, 'idx': 200809}
# points in region:  99676
SQ:  127450
------------ end of loop ----------------
{'position': array([ 0.39951098,  0.98626155, -0.4698206 ]), 'n': array([ 0.75883728,  0.16673987, -0.6295743 ]), 'c': 1.34553420

KeyboardInterrupt: 